Hafta 2: Kod ve Veri için Test Stratejileri

**Dersin Hedefleri:**
1.  Yazılım testinin veri bilimi projelerindeki önemini kavramak.
2.  Test Güdümlü Geliştirme (TDD) döngüsünü (Red-Green-Refactor) anlamak ve uygulamak.
3.  `pytest` kütüphanesini kullanarak etkin birim testleri (unit tests) yazmak.
4.  Veri bilimine özgü testler: Veri doğrulama (data validation) testleri ile veri kalitesini garanti altına almak.
5.  Bu testleri, bir önceki hafta öğrendiğimiz Git iş akışlarına entegre etme mantığını anlamak.

## 1. Neden Test Yazmalıyız?

Bir önceki hafta, kodumuzun geçmişini yönetmeyi öğrendik. Peki yazdığımız kodun **doğru çalıştığından** nasıl emin olabiliriz?

- **Güvenilirlik:** Testler, kodunuzun beklenen girdiler için beklenen çıktıları ürettiğini kanıtlar. Bu, özellikle karmaşık veri işleme pipeline'larında kritiktir.
- **Regresyon Önleme:** Yeni bir özellik eklediğinizde veya mevcut kodu iyileştirdiğinizde (refactoring), farkında olmadan eski ve çalışan bir özelliği bozabilirsiniz. Kapsamlı bir test paketi, bu tür "regresyon" hatalarını anında yakalar.
- **Canlı Dokümantasyon:** Testler, bir fonksiyonun nasıl kullanılması gerektiğini ve ne yapması gerektiğini gösteren en iyi dokümantasyondur. Kodun kendisi eskir ama testler güncel kalmak zorundadır.
- **Refactoring Cesareti:** İyi test edilmiş bir kod tabanını iyileştirmek ve yeniden yapılandırmak çok daha kolay ve güvenlidir. Testler sizin güvenlik ağınızdır.

## 2. Test Güdümlü Geliştirme (TDD)

TDD, yazılım geliştirme sürecini tersine çeviren bir metodolojidir. Önce kodu yazıp sonra test etmek yerine, **önce test yazılır**.

**TDD Döngüsü:**

1.  **RED:** Yeni bir özellik için **başarısız olacak** bir test yaz. Testi çalıştır ve başarısız olduğunu gör. Bu, testin kendisinin doğru çalıştığını (yani olmayan bir şeyi "başarılı" göstermediğini) kanıtlar.
2.  **GREEN:** Testi **başarılı kılacak en basit** kodu yaz. Bu aşamada kodun ne kadar "güzel" veya "verimli" olduğu önemli değildir. Amaç, sadece testi geçmektir. Testi tekrar çalıştır ve başarılı olduğunu gör.
3.  **REFACTOR:** Artık çalışan bir kodun ve onu koruyan bir testin var. Kodunu daha okunabilir, daha verimli veya daha iyi tasarlanmış hale getirmek için güvenle yeniden yapılandır. Her adımdan sonra testleri çalıştırarak hiçbir şeyi bozmadığından emin ol.

Bu döngü, daha modüler, daha test edilebilir ve daha sağlam bir kod tabanı oluşturmayı teşvik eder.

## 3. `pytest` ile Pratik Uygulama

`pytest`, Python için standart haline gelmiş, basit ve güçlü bir test çatısıdır.

**Kurulum:**
```bash
pip install pytest
```

**Temel Kurallar:**
- Test dosyalarının adları `test_*.py` veya `*_test.py` ile başlamalıdır.
- Test fonksiyonlarının adları `test_*` ile başlamalıdır.
- Testlerdeki doğrulamalar basit `assert` ifadeleri ile yapılır.

### Uygulama: Veri Temizleme Fonksiyonunu Test Etme

Senaryomuz: Bir hasta kayıt sisteminden gelen verileri temizleyen bir fonksiyon yazmamız gerekiyor. Bu verilerde hatalar olabilir (örn. negatif yaş, hatalı kan basıncı değeri).

İlk olarak, test dosyamızı ve başarısız olacak testimizi (RED) oluşturalım.

In [ ]:
# Proje yapısını simüle edelim
import os
import shutil

# Proje klasörlerini oluştur
project_root = "hafta2_projesi"
src_dir = os.path.join(project_root, "src")
tests_dir = os.path.join(project_root, "tests")

if os.path.exists(project_root):
    shutil.rmtree(project_root)

os.makedirs(src_dir)
os.makedirs(tests_dir)

# __init__.py dosyaları ile Python paketleri oluşturalım
open(os.path.join(src_dir, "__init__.py"), 'w').close()
open(os.path.join(tests_dir, "__init__.py"), 'w').close()


In [ ]:

# --- RED: Başarısız olacak testi yaz ---
# tests/test_data_cleaning.py
test_file_content = """
import pytest
import pandas as pd
from src.data_cleaning import clean_patient_data

def test_clean_patient_data_removes_negative_age():
    # 1. Test için sentetik, sorunlu veri oluştur
    dirty_data = pd.DataFrame({
        'patient_id': [1, 2, 3],
        'age': [34, -5, 45], # Negatif yaş hatası
        'blood_pressure': ['120/80', '130/85', '110/70']
    })
    
    # 2. Temizleme fonksiyonunu çağır
    cleaned_data = clean_patient_data(dirty_data)
    
    # 3. Doğrula (Assert): Temizlenmiş veride negatif yaş kalmamalı
    assert (cleaned_data['age'] >= 0).all()
"""

with open(os.path.join(tests_dir, "test_data_cleaning.py"), "w") as f:
    f.write(test_file_content)

# Henüz fonksiyonu yazmadığımız için bu test başarısız olacak.
# İlk olarak src/data_cleaning.py dosyası boş bir fonksiyonla oluşturulur.
cleaning_script_content_initial = """
import pandas as pd

def clean_patient_data(df: pd.DataFrame) -> pd.DataFrame:
    # Henüz bir şey yapmıyor
    return df
"""
with open(os.path.join(src_dir, "data_cleaning.py"), "w") as f:
    f.write(cleaning_script_content_initial)

# Testi çalıştır (Normalde terminalden `pytest` komutu ile yapılır)
# Burada subprocess ile simüle ediyoruz.
# Not: Bu, fonksiyonun henüz negatif yaşları düzeltmediği için bir AssertionError fırlatacaktır.
print("--- TDD Adım 1: RED ---")
# !pytest {project_root}  # Jupyter/IPython'da bu şekilde çalıştırılabilir.
# subprocess ile çalıştırma:
import subprocess
result = subprocess.run(["pytest", project_root], capture_output=True, text=True)
print(result.stdout)
print(result.stderr)


# --- GREEN: Testi geçecek en basit kod ---
print("\n--- TDD Adım 2: GREEN ---")
cleaning_script_content_green = """
import pandas as pd
import numpy as np

def clean_patient_data(df: pd.DataFrame) -> pd.DataFrame:
    df_copy = df.copy()
    # Negatif yaşları NaN ile değiştir (veya 0 ile, veya ortalama ile - şimdilik en basiti)
    df_copy.loc[df_copy['age'] < 0, 'age'] = np.nan
    return df_copy
"""
with open(os.path.join(src_dir, "data_cleaning.py"), "w") as f:
    f.write(cleaning_script_content_green)

# Testi tekrar çalıştır. Şimdi başarılı olmalı.
result = subprocess.run(["pytest", project_root], capture_output=True, text=True)
print(result.stdout)
print(result.stderr)


# --- REFACTOR: Kod iyileştirme ---
print("\n--- TDD Adım 3: REFACTOR ---")
# Negatif yaşları NaN yapmak yerine ortalama ile doldurma alternatif bir strateji olabilir.
# Test ve kod bu yeni mantığa göre güncellenebilir.
# Bu örnek için kodumuz yeterince basit, refactor adımını atlıyoruz ama mantık bu.
print("Kodumuz basit olduğu için bu adımda değişiklik yapılmadı.")

## 4. Veri Doğrulama Testleri

Geleneksel birim testleri fonksiyonların mantığını test eder. Ancak veri biliminde, **verinin kendisi de hatalar içerebilir**. Veri doğrulama testleri, veri kalitesini, yapısını ve istatistiksel özelliklerini kontrol eder.

**Yaygın Veri Doğrulama Kontrolleri:**
- **Şema Kontrolü:** Gerekli sütunlar var mı? Sütun adları doğru mu? Veri tipleri (int, float, object) beklendiği gibi mi?
- **Boş Değer Kontrolü:** Belirli sütunlarda boş (null/NaN) değer olmamalı.
- **Aralık Kontrolü:** Değerler mantıklı bir aralıkta mı? (örn: yaş > 0, yüzde 0-100 arası)
- **Kategorik Değer Kontrolü:** Kategorik bir sütundaki değerler, izin verilen bir setin içinde mi? (örn: `cinsiyet` sütunu sadece 'Erkek', 'Kadın' içermeli)

### Uygulama: `pydantic` ile Veri Şeması Doğrulama

`pydantic` gibi kütüphaneler, Python veri sınıfları kullanarak veri şemalarını tanımlamayı ve doğrulamayı çok kolaylaştırır.

**Kurulum:**
```bash
pip install pydantic
```

In [ ]:
import pandas as pd
from pydantic import BaseModel, Field, ValidationError
from typing import List

# 1. Beklenen veri şemasını bir Pydantic modeli ile tanımla
class PatientRecord(BaseModel):
    patient_id: int
    age: int = Field(gt=0, le=120) # gt: greater than, le: less than or equal
    gender: str
    blood_pressure: str

# 2. Tüm DataFrame'i doğrulayacak bir model oluştur
class PatientData(BaseModel):
    records: List[PatientRecord]

# 3. Sentetik Veri Oluşturma
# a) Geçerli Veri
valid_df = pd.DataFrame([
    {'patient_id': 101, 'age': 45, 'gender': 'Female', 'blood_pressure': '120/80'},
    {'patient_id': 102, 'age': 52, 'gender': 'Male', 'blood_pressure': '140/90'}
])

# b) Geçersiz Veri
invalid_df = pd.DataFrame([
    {'patient_id': 201, 'age': -10, 'gender': 'Male', 'blood_pressure': '130/85'}, # Negatif yaş
    {'patient_id': 202, 'age': 30, 'gender': 'Other', 'blood_pressure': '115/75'} # Geçersiz 'gender' varsayımı
])


# 4. Doğrulama Fonksiyonu
def validate_data_schema(df: pd.DataFrame) -> bool:
    """Validates a DataFrame against the PatientData Pydantic model."""
    try:
        # Pydantic'in bekledeği format için DataFrame'i dict listesine çevir
        data_dict = {"records": df.to_dict(orient="records")}
        PatientData.parse_obj(data_dict)
        print("Veri şeması doğrulandı: Başarılı!")
        return True
    except ValidationError as e:
        print("Veri şeması hatası!")
        print(e)
        return False

print("--- Geçerli Veri Testi ---")
validate_data_schema(valid_df)

print("\n--- Geçersiz Veri Testi ---")
validate_data_schema(invalid_df)

# Temizlik
shutil.rmtree(project_root)

## 5. Model Hiperparametre Optimizasyonu için Test Stratejileri

Veri bilimi projelerinde model performansını optimize etmek için hiperparametre ayarlaması kritik öneme sahiptir. Grid Search ve Random Search gibi sistematik yaklaşımlar, hem objektif model karşılaştırması hem de tekrarlanabilir sonuçlar sağlar.

### 5.1. Grid Search: Deterministik Hiperparametre Keşfi

Grid Search, hiperparametre uzayında önceden tanımlanmış bir ızgara üzerinde kapsamlı arama yapar. Her parametre kombinasyonu test edilir ve çapraz doğrulama ile değerlendirilir.

**Matematiksel Formalizasyon:**
Hiperparametre uzayı Θ = {θ₁, θ₂, ..., θₚ} olsun. Grid Search için:
- Her θᵢ için ayrı değer kümesi: Θᵢ = {θᵢ¹, θᵢ², ..., θᵢⁿⁱ}
- Toplam arama uzayı: |Θ₁| × |Θ₂| × ... × |Θₚ| kombinasyon
- Amaç: arg min_θ∈Θ L(θ) (kayıp fonksiyonu minimizasyonu)

In [ ]:
import numpy as np
import pandas as pd
from sklearn.datasets import make_classification
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV, cross_val_score
from sklearn.metrics import accuracy_score, precision_score, recall_score
from sklearn.model_selection import train_test_split
import pytest

# Deneysel veri seti oluştur
X, y = make_classification(n_samples=1000, n_features=10, n_informative=7,
                          n_redundant=3, random_state=42)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Grid Search implementasyonu
def test_grid_search_systematic():
    """Grid Search'ün sistematik hiperparametre tarama yaklaşımını test eder."""

    # Hiperparametre ızgarası tanımla
    param_grid = {
        'n_estimators': [50, 100, 200],
        'max_depth': [3, 5, 7, None],
        'min_samples_split': [2, 5, 10]
    }

    # Grid Search nesnesi oluştur
    rf = RandomForestClassifier(random_state=42)
    grid_search = GridSearchCV(
        estimator=rf,
        param_grid=param_grid,
        cv=5,  # 5-katlı çapraz doğrulama
        scoring='accuracy',
        n_jobs=-1,
        verbose=0
    )

    # Model eğitimi ve hiperparametre optimizasyonu
    grid_search.fit(X_train, y_train)

    # En iyi parametreleri al
    best_params = grid_search.best_params_
    best_score = grid_search.best_score_

    # Test performansı
    best_model = grid_search.best_estimator_
    y_pred = best_model.predict(X_test)
    test_accuracy = accuracy_score(y_test, y_pred)

    # Doğrulama testleri
    assert best_score > 0.7, "Grid Search sonucu minimum performans kriterini karşılamalı"
    assert test_accuracy > 0.7, "Test seti performansı kabul edilebilir seviyede olmalı"
    assert len(best_params) == 3, "En iyi parametre seti tüm hiperparametreleri içermeli"

    print(f"Grid Search Sonuçları:")
    print(f"En iyi parametreler: {best_params}")
    print(f"En iyi CV skoru: {best_score:.4f}")
    print(f"Test doğruluğu: {test_accuracy:.4f}")

    return best_params, best_score, test_accuracy

# Test fonksiyonunu çalıştır
grid_results = test_grid_search_systematic()

### 5.2. Random Search: Stokastik Hiperparametre Keşfi

Random Search, hiperparametre uzayından rastgele örnekleme yapar. Bergstra & Bengio (2012) çalışması, yüksek boyutlu uzaylarda Random Search'ün Grid Search'ten daha etkili olabileceğini göstermiştir.

**Teorik Avantajlar:**
- Sürekli parametreler için daha uygun
- Hesaplama maliyeti sabit (n iterasyon)
- Yüksek boyutlu uzaylarda daha etkili keşif
- Önemsiz parametrelere daha az zaman harcar

In [ ]:
from scipy.stats import randint, uniform

def test_random_search_efficiency():
    """Random Search'ün verimlilik ve keşif kapasitesini test eder."""

    # Sürekli ve ayrık parametreler için dağılım tanımla
    param_distributions = {
        'n_estimators': randint(50, 300),      # Ayrık dağılım
        'max_depth': randint(3, 15),          # Ayrık dağılım
        'min_samples_split': randint(2, 20),  # Ayrık dağılım
        'min_samples_leaf': randint(1, 10),   # Ayrık dağılım
        'max_features': uniform(0.1, 0.9)     # Sürekli dağılım
    }

    # Random Search nesnesi oluştur
    rf = RandomForestClassifier(random_state=42)
    random_search = RandomizedSearchCV(
        estimator=rf,
        param_distributions=param_distributions,
        n_iter=50,  # 50 rastgele kombinasyon dene
        cv=5,
        scoring='accuracy',
        n_jobs=-1,
        verbose=0,
        random_state=42
    )

    # Model eğitimi
    random_search.fit(X_train, y_train)

    # Sonuçları analiz et
    best_params = random_search.best_params_
    best_score = random_search.best_score_

    # Test performansı
    best_model = random_search.best_estimator_
    y_pred = best_model.predict(X_test)
    test_accuracy = accuracy_score(y_test, y_pred)

    # Keşfedilen parametre uzayının çeşitliliğini değerlendir
    results_df = pd.DataFrame(random_search.cv_results_)
    param_variance = results_df[['param_n_estimators', 'param_max_depth']].var()

    # Doğrulama testleri
    assert best_score > 0.7, "Random Search performans kriterini karşılamalı"
    assert test_accuracy > 0.7, "Test performansı kabul edilebilir seviyede olmalı"
    assert param_variance.mean() > 0, "Parametre uzayında yeterli çeşitlilik keşfedilmeli"

    print(f"\nRandom Search Sonuçları:")
    print(f"En iyi parametreler: {best_params}")
    print(f"En iyi CV skoru: {best_score:.4f}")
    print(f"Test doğruluğu: {test_accuracy:.4f}")
    print(f"Parametre çeşitliliği (varyans): {param_variance.mean():.2f}")

    return best_params, best_score, test_accuracy

# Test fonksiyonunu çalıştır
random_results = test_random_search_efficiency()

### 5.3. Karşılaştırmalı Analiz ve Metodolojik Değerlendirme

Grid Search ve Random Search yaklaşımlarının sistematik karşılaştırması, her metodun güçlü ve zayıf yönlerini ortaya koyar.

In [ ]:
def test_search_methodology_comparison():
    """Grid Search ve Random Search metodolojilerini karşılaştırır."""

    # Aynı temel hiperparametre uzayı için her iki metodu test et
    base_param_space = {
        'n_estimators': [50, 100, 150],
        'max_depth': [3, 5, 7],
        'min_samples_split': [2, 5, 10]
    }

    # Grid Search
    rf_grid = RandomForestClassifier(random_state=42)
    grid_search = GridSearchCV(rf_grid, base_param_space, cv=3, scoring='accuracy')

    # Random Search için eşdeğer dağılım
    random_param_space = {
        'n_estimators': [50, 100, 150],
        'max_depth': [3, 5, 7],
        'min_samples_split': [2, 5, 10]
    }

    rf_random = RandomForestClassifier(random_state=42)
    random_search = RandomizedSearchCV(
        rf_random, random_param_space, n_iter=27,  # Tüm kombinasyonları kapsa
        cv=3, scoring='accuracy', random_state=42
    )

    # Her iki metodu eğit
    import time

    start_time = time.time()
    grid_search.fit(X_train, y_train)
    grid_time = time.time() - start_time

    start_time = time.time()
    random_search.fit(X_train, y_train)
    random_time = time.time() - start_time

    # Performans karşılaştırması
    grid_performance = grid_search.best_score_
    random_performance = random_search.best_score_

    # Test sonuçları
    assert abs(grid_performance - random_performance) < 0.05, "Performans farkı minimal olmalı"
    assert grid_time > 0 and random_time > 0, "Her iki metod da ölçülebilir sürede tamamlanmalı"

    print(f"\nMetodolojik Karşılaştırma:")
    print(f"Grid Search - Performans: {grid_performance:.4f}, Süre: {grid_time:.2f}s")
    print(f"Random Search - Performans: {random_performance:.4f}, Süre: {random_time:.2f}s")
    print(f"Performans farkı: {abs(grid_performance - random_performance):.4f}")

    # Metodolojik öneriler
    if random_performance >= grid_performance * 0.95 and random_time < grid_time:
        print("Öneri: Bu veri seti için Random Search daha verimli")
    else:
        print("Öneri: Grid Search daha kapsamlı keşif sağlıyor")

    return {
        'grid': {'performance': grid_performance, 'time': grid_time},
        'random': {'performance': random_performance, 'time': random_time}
    }

# Karşılaştırma testini çalıştır
comparison_results = test_search_methodology_comparison()

### 5.4. Pratik Uygulama Rehberi

**Grid Search Kullanım Senaryoları:**
- Düşük boyutlu hiperparametre uzayı (< 4 parametre)
- Ayrık parametre değerleri
- Kapsamlı keşif gereksinimi
- Hesaplama kaynakları bol

**Random Search Kullanım Senaryoları:**
- Yüksek boyutlu hiperparametre uzayı (> 4 parametre)
- Sürekli parametre dağılımları
- Sınırlı hesaplama bütçesi
- Hızlı prototipleme gereksinimi

In [ ]:
def hyperparameter_optimization_strategy(n_params, computation_budget, param_types):
    """Verilen kısıtlar için optimal hiperparametre optimizasyon stratejisi önerir."""

    if n_params <= 3 and computation_budget == 'high':
        return "Grid Search - Kapsamlı keşif için ideal"
    elif n_params > 4 or computation_budget == 'low':
        return "Random Search - Verimli keşif için ideal"
    elif 'continuous' in param_types:
        return "Random Search - Sürekli parametreler için daha uygun"
    else:
        return "Grid Search - Ayrık parametreler için sistematik yaklaşım"

# Strateji örnekleri
print("\nHiperparametre Optimizasyon Stratejisi Önerileri:")
print("Düşük boyut + Yüksek bütçe:", hyperparameter_optimization_strategy(3, 'high', ['discrete']))
print("Yüksek boyut + Düşük bütçe:", hyperparameter_optimization_strategy(6, 'low', ['discrete']))
print("Sürekli parametreler:", hyperparameter_optimization_strategy(4, 'medium', ['continuous']))

### Alıştırma 3: Kendi Veri Doğrulama Testinizi Yazın

1.  Bir e-ticaret sitesinden geldiğini varsaydığınız siparişler için bir `pydantic` modeli (`OrderItem`) oluşturun.
2.  Bu model şu alanları içermeli:
    *   `order_id` (string)
    *   `product_id` (string)
    *   `quantity` (integer, 0'dan büyük olmalı)
    *   `price_usd` (float, 0'dan büyük olmalı)
    *   `status` (string, ve sadece 'shipped', 'pending', 'cancelled' değerlerini alabilmeli. `pydantic.validator` kullanmayı araştırın!)
3.  Hem geçerli hem de geçersiz veriler içeren iki `pandas.DataFrame` oluşturun.
4.  Bu DataFrame'leri `OrderItem` modelinize karşı doğrulayan bir fonksiyon yazın ve sonuçları gözlemleyin.

### Haftanın Özeti

Kod kalitesi ve güvenilirliğinin temel disiplini olan test yazma yöntemleri incelendi.

- **TDD**, sağlam ve modüler kod geliştirme için güçlü bir metodoloji sunar.
- **`pytest`**, Python'da test yazmayı basit ve etkili hale getirir.
- **Veri Doğrulama**, veri bilimi projelerinin kritik bileşenidir ve `pydantic` gibi araçlar bu süreci kolaylaştırır.
- **Grid Search ve Random Search**, model hiperparametre optimizasyonu için sistematik ve test edilebilir yaklaşımlar sunar.
- **Hiperparametre optimizasyonu**, tekrarlanabilir ve objektif model değerlendirmesi için kritik öneme sahiptir.

### Devam Eden Konular

Kod versiyon yönetimi (Hafta 1) ve test stratejileri (Hafta 2) temellerinin ardından, **Özellik Mühendisliği (Feature Engineering)** konusu ele alınacaktır. Test süreçleri, yeni özellik yaratma aşamalarında mevcut pipeline'ın korunmasını sağlar.

---

### **Hafta 3: Özellik Mühendisliği ve Seçimi**
```python
# %% [markdown]